In [13]:
import json 
import re
import time
import requests
import pandas as pd
from deep_translator import GoogleTranslator
import base64

# 🔹 API Key & Secret
CLIENT_ID = "f234667d9b504925863936ec96d55fed"
CLIENT_SECRET = "626d8b976c8a48ab9f162c0134015560"

# FatSecret data 수집

In [14]:
auth_string = f"{CLIENT_ID}:{CLIENT_SECRET}"
auth_bytes = auth_string.encode("utf-8")
auth_base64 = base64.b64encode(auth_bytes).decode("utf-8")

def get_access_token():
    url = "https://oauth.fatsecret.com/connect/token"
    headers = {
        "Authorization": f"Basic {auth_base64}",
        "Content-Type": "application/x-www-form-urlencoded"
    }
    data = {"grant_type": "client_credentials"}
    response = requests.post(url, headers=headers, data=data)
    return response.json().get("access_token")

access_token = get_access_token()

# ✅ 한글 → 영어 번역 캐시
food_translation = {}

def translate_food_name(korean_name):
    if korean_name in food_translation:
        return food_translation[korean_name]

    english_name = GoogleTranslator(source="ko", target="en").translate(korean_name)
    food_translation[korean_name] = english_name  # ✅ 변환된 값 저장
    print(f"🌍 번역: {korean_name} → {english_name}")
    return english_name

# ✅ FatSecret 음식 검색 함수
def search_food(query):
    query_eng = translate_food_name(query)  # ✅ 한글 → 영어 자동 변환
    print(f"🔍 검색어 확인: {query} -> {query_eng}")  # ✅ 번역 확인
    
    url = "https://platform.fatsecret.com/rest/server.api"
    headers = {"Authorization": f"Bearer {access_token}"}
    params = {
        "method": "foods.search",
        "format": "json",
        "search_expression": query_eng
    }

    response = requests.get(url, headers=headers, params=params)
    
    if response.status_code != 200:
        print(f"❌ 검색 실패! 상태 코드: {response.status_code}, 응답: {response.text}")
        return None

    result = response.json()
    print(f"📩 API 응답: {json.dumps(result, indent=2, ensure_ascii=False)}")  # ✅ API 응답 확인

    food_list = result.get("foods", {}).get("food", [])

    if not food_list:  # ✅ 빈 리스트 예외 처리
        print(f"🚨 {query}({query_eng}): 검색 결과 없음!")
        return None

    if isinstance(food_list, dict):  # 🔸 API가 단일 음식만 반환할 경우 처리
        food_list = [food_list]  # 리스트로 변환

    first_food = food_list[0]  # ✅ 첫 번째 검색 결과 가져오기
    food_name = first_food.get("food_name", "N/A")
    food_description = first_food.get("food_description", "")

    print(f"📝 검색된 음식: {food_name} | 설명: {food_description}")  # ✅ 결과 확인
    
    match = re.search(
        r'Per ([\d.]+\s?[a-zA-Z]*) - Calories:\s*([\d.]+)kcal\s*\|\s*Fat:\s*([\d.]+)g\s*\|\s*Carbs:\s*([\d.]+)g\s*\|\s*Protein:\s*([\d.]+)g',
        food_description
    )

    if match:
        serving_size, calories, fat, carbs, protein = match.groups()  # ✅ 순서 맞게 변경
    else:
        print(f"⚠️ 정규식 매칭 실패: {food_description}")  # ✅ 정규식 문제 확인
        serving_size = calories = fat = carbs = protein = "N/A"

    return {
        "food_name": food_name,
        "calories": calories,
        "carbohydrate": carbs,
        "protein": protein,
        "fat": fat,
        "serving_size": serving_size  # ✅ 1회 섭취량 추가
    }

# ✅ CSV 파일에서 음식명 가져오기
df = pd.read_csv("data/merged_food_data.csv") 
food_names = df["식품명"].tolist()

# ✅ 검색 결과 저장할 리스트
food_results = []

# ✅ 음식명으로 FatSecret 검색 후 결과 저장
for food in food_names:
    print(f"🔍 검색 중: {food}")
    result = search_food(food)
    if result:
        food_results.append({
            "식품명(한글)": food,
            "칼로리": result["calories"],
            "탄수화물": result["carbohydrate"],
            "단백질": result["protein"],
            "지방": result["fat"],
            "1회 섭취량": result["serving_size"]
        })
    else:
        print(f"🚨 {food} 검색 실패!")

    time.sleep(1)  # API 호출 제한 방지 (1초 대기)

# ✅ 결과를 CSV 파일로 저장
output_df = pd.DataFrame(food_results)
output_df.to_csv("data/food_nutrition_data.csv", index=False, encoding="utf-8-sig")

print("✅ 모든 음식 검색 완료! 결과가 'data/food_nutrition_data.csv'에 저장되었습니다.")

🔍 검색 중: 가래떡
🌍 번역: 가래떡 → Sputum
🔍 검색어 확인: 가래떡 -> Sputum
📩 API 응답: {
  "foods": {
    "max_results": "20",
    "page_number": "0",
    "total_results": "0"
  }
}
🚨 가래떡(Sputum): 검색 결과 없음!
🚨 가래떡 검색 실패!
🔍 검색 중: 가리비
🌍 번역: 가리비 → scallop
🔍 검색어 확인: 가리비 -> scallop
📩 API 응답: {
  "foods": {
    "food": [
      {
        "food_description": "Per 1086g - Calories: 2358kcal | Fat: 119.08g | Carbs: 113.97g | Protein: 197.08g",
        "food_id": "2173",
        "food_name": "Scallops",
        "food_type": "Generic",
        "food_url": "https://www.fatsecret.com/calories-nutrition/generic/scallops-cooked"
      },
      {
        "brand_name": "Pacific Seafood",
        "food_description": "Per 4 oz - Calories: 80kcal | Fat: 0.50g | Carbs: 4.00g | Protein: 14.00g",
        "food_id": "61862803",
        "food_name": "Scallops",
        "food_type": "Brand",
        "food_url": "https://www.fatsecret.com/calories-nutrition/pacific-seafood/scallops"
      },
      {
        "food_description": "Per 706